In [2]:
import pandas as pd
df = pd.read_csv("Training_Data.csv")
headers = df.columns
print(headers)


Index(['billingstreet', 'billingcity', 'billingstate', 'billingpostalcode',
       'billingcountry'],
      dtype='object')


Data Preprocessing

In [3]:
import pandas as pd

# Load the Excel sheet
file_path = 'Training_Data.csv'  # Replace with your actual file path
sheet_name = 'Sheet2'  # Update if your sheet has a different name
df = pd.read_csv(file_path)

# List of address columns
address_columns = ['billingstreet', 'billingcity', 'billingstate', 'billingpostalcode', 'billingcountry']

# Clean each column by removing extra spaces
for column in address_columns:
    if column in df.columns:
        df[column] = df[column].astype(str).str.strip()  # Convert to string if needed and strip spaces

# Save the cleaned data to a new Excel file
cleaned_file_path = 'cleaned_data.csv'
df.to_csv(cleaned_file_path, index=False)

print(f"Data cleaning complete. Cleaned data saved to {cleaned_file_path}")


Data cleaning complete. Cleaned data saved to cleaned_data.csv


In [15]:
import pandas as pd
from sentence_transformers import SentenceTransformer
import chromadb
from chromadb.config import Settings

# Load the address data
file_path = 'cleaned_data.csv'  # Path to your cleaned address file
df = pd.read_csv(file_path)

# Combine address columns into a single string for embedding
df['full_address'] = df[['billingstreet', 'billingcity', 'billingstate', 'billingpostalcode', 'billingcountry']].astype(str).agg(', '.join, axis=1)

# Initialize a Sentence Transformer model for embedding
model = SentenceTransformer('all-MiniLM-L6-v2')  # You can change the model if needed

# Generate embeddings for each address
embeddings = model.encode(df['full_address'].tolist())

# Initialize ChromaDB client
# client = chromadb.PersistentClient(Settings())
client = chromadb.PersistentClient('vectorstore')

# Create a collection for the addresses
collection_name = "address_embeddings"
collection = client.get_or_create_collection(collection_name)

# Insert data and embeddings into ChromaDB
for i, (address, embedding) in enumerate(zip(df['full_address'], embeddings)):
    collection.add(
        ids=[str(i)],  # Unique ID for each record
        embeddings=[embedding],
        metadatas=[{'address': address}]
    )

print("ChromaDB vector database training completed.")


ChromaDB vector database training completed.


In [19]:
import chromadb
from sentence_transformers import SentenceTransformer

# Initialize the ChromaDB Persistent Client and load the collection
client = chromadb.PersistentClient('vectorstore')
collection_name = "address_embeddings"
collection = client.get_collection(collection_name)

# Initialize the same Sentence Transformer model used for training
model = SentenceTransformer('all-MiniLM-L6-v2')  # Must match the model used during training

# Define the address to query
query_address = "650 Davis St"
query_embedding = model.encode([query_address])[0]  # Generate embedding for the query

# Perform the query to find similar addresses
n_results = 1  # Number of closest matches to retrieve
results = collection.query(
    query_embeddings=[query_embedding],  # Embedding to search with
    n_results=n_results
)

# Display the results
print(f"Top {n_results} similar addresses for '{query_address}':\n")
for i, (result_id, metadata, distance) in enumerate(zip(results['ids'][0], results['metadatas'][0], results['distances'][0])):
    print(f"Result {i+1}:")
    print("ID:", result_id)
    print("Address:", metadata['address'])
    print("Similarity Score:", distance)  # Lower score indicates higher similarity
    print("\n")


Top 1 similar addresses for '650 Davis St':

Result 1:
ID: 79
Address: 650 Davis St, San Francisco, California, 94111-1981, United States
Similarity Score: 0.43980643153190613




In [5]:
import pandas as pd
from sentence_transformers import SentenceTransformer
import chromadb
from chromadb.config import Settings

# Load the address data
file_path = 'cleaned_data.csv'  # Path to your cleaned address file
df = pd.read_csv(file_path)

# Initialize a Sentence Transformer model for embedding
model = SentenceTransformer('all-MiniLM-L6-v2')

# Combine address columns into a single string for embedding
df['full_address'] = df[['billingstreet', 'billingcity', 'billingstate', 'billingpostalcode', 'billingcountry']].astype(str).agg(', '.join, axis=1)

# Generate embeddings for each full address
embeddings = model.encode(df['full_address'].tolist())

# Initialize ChromaDB Persistent Client
client = chromadb.PersistentClient('vectorstore')

# Create a collection for the addresses
collection_name = "address_embeddings"
collection = client.get_or_create_collection(collection_name)

# Insert data and embeddings into ChromaDB
for i, row in df.iterrows():
    # Metadata with individual address fields
    metadata = {
        'Billing Street': row['billingstreet'],
        'Billing City': row['billingcity'],
        'Billing State': row['billingstate'],
        'Postal Code': row['billingpostalcode'],
        'Country': row['billingcountry']
    }

    # Add the embedding and metadata to the collection
    collection.add(
        ids=[str(i)],  # Unique ID for each record
        embeddings=[embeddings[i]],
        metadatas=[metadata]
    )

print("ChromaDB vector database training completed with full address embedding.")


Add of existing embedding ID: 0
Insert of existing embedding ID: 0
Add of existing embedding ID: 1
Insert of existing embedding ID: 1
Add of existing embedding ID: 2
Insert of existing embedding ID: 2
Add of existing embedding ID: 3
Insert of existing embedding ID: 3
Add of existing embedding ID: 4
Insert of existing embedding ID: 4
Add of existing embedding ID: 5
Insert of existing embedding ID: 5
Add of existing embedding ID: 6
Insert of existing embedding ID: 6
Add of existing embedding ID: 7
Insert of existing embedding ID: 7
Add of existing embedding ID: 8
Insert of existing embedding ID: 8
Add of existing embedding ID: 9
Insert of existing embedding ID: 9
Add of existing embedding ID: 10
Insert of existing embedding ID: 10
Add of existing embedding ID: 11
Insert of existing embedding ID: 11
Add of existing embedding ID: 12
Insert of existing embedding ID: 12
Add of existing embedding ID: 13
Insert of existing embedding ID: 13
Add of existing embedding ID: 14
Insert of existing em

ChromaDB vector database training completed with full address embedding.


In [1]:
import chromadb
from chromadb.config import Settings

# Initialize ChromaDB Persistent Client
client = chromadb.PersistentClient('vectorstore')

# Create a collection for the addresses
collection_name = "address_embeddings"
collection = client.get_or_create_collection(collection_name)

In [4]:
from sentence_transformers import SentenceTransformer

# Initialize the same Sentence Transformer model used for training
model = SentenceTransformer('all-MiniLM-L6-v2')

# Define the address to query
query_address = "123 Main St, Springfield, IL, 62701, USA"
query_embedding = model.encode([query_address])[0]  # Generate embedding for the query

# Number of results to retrieve
n_results = 5

# Perform the query to find similar addresses
results = collection.query(
    query_embeddings=[query_embedding],  # Embedding to search with
    n_results=n_results
)

# Display the results with individual address fields
print(f"Top {n_results} similar addresses for '{query_address}':\n")
for i, (result_id, metadata, distance) in enumerate(zip(results['ids'][0], results['metadatas'][0], results['distances'][0])):
    print(f"Result {i+1}:")
    print("ID:", result_id)
    print("Metadata:", metadata)

    # print(results)
    # print("Billing Street:", metadata['Billing Street'])
    # print("Billing City:", metadata['Billing City'])
    # print("Billing State:", metadata['Billing State'])
    # print("Postal Code:", metadata['Postal Code'])
    # print("Country:", metadata['Country'])
    # print("Similarity Score:", distance)  # Lower score indicates higher similarity
    # print("\n")


Top 5 similar addresses for '123 Main St, Springfield, IL, 62701, USA':

Result 1:
ID: 23835
Metadata: {'address': '701 N 1ST St, Springfield, Illinois, 62781-0002, United States'}
Result 2:
ID: 16739
Metadata: {'address': '505 N MacArthur Blvd, Springfield, Illinois, 62702-2313, United States'}
Result 3:
ID: 23192
Metadata: {'address': '1500 Main St, Springfield, Massachusetts, 01103, United States'}
Result 4:
ID: 34981
Metadata: {'address': '1350 Main St Ste 508, Springfield, Massachusetts, 01103-1664, United States'}
Result 5:
ID: 41598
Metadata: {'address': '5402 Fremont St, Springfield, Virginia, 22151-3127, United States'}
